# Setup

In [92]:
import pandas as pd
import altair as vg
import seaborn as sns
import numpy as np
import math as m
from itertools import combinations

In [93]:
import warnings
warnings.simplefilter('ignore')

# Data Prep

In [94]:
filepath = '../data/Dados_v3.xlsx'
df = pd.read_excel(filepath)

In [95]:
df.head()

Sigla        Nome  Latitude  Longitude   Município        Modal       Rio  \
0  AM-000      MANAUS -3.138087 -60.027484      Manaus          NaN     Negro   
1  AM-083     SACAMBU -3.272442 -60.952701  Manacapuru  Hidroviário  Solimões   
2  AM-028    CAMPINAS -3.278834 -61.099313  Manacapuru  Hidroviário  Solimões   
3  AM-023  CAAPIRANGA -3.324601 -61.212903  Manacapuru     Gasoduto  Solimões   
4  AM-004       ANAMÃ -3.572283 -61.407035       Anamã     Gasoduto  Solimões   

   Latitude_2  Longitude_2                                                OBS  \
0   -3.138087   -60.027484                                    Porto de Manaus   
1   -3.274633   -60.933956  Lago Cabaliana, UTE Sacambu; este nó será agre...   
2   -3.278834   -61.099313  Lago Cabaliana + Rio Paraná do Aramã; este nó ...   
3   -3.278834   -61.099313  Verificar acesso ao município; supondo entrega...   
4   -3.572283   -61.407035                                                NaN   

   Considerar  Carga_2023  Carga_2024            GN          GNL  \
0           0           0           0           NaN          NaN   
1           0        1487        1511  4.558757e+05   759.792829   
2           1        1085        1099  3.315734e+05   552.622316   
3           0        9984       10253  3.093378e+06  5155.629306   
4           0       12675       13347  4.026852e+06  6711.419520   

   Conteineres/Ano  
0              NaN  
1        15.195857  
2        11.052446  
3       103.112586  
4       134.228390

In [96]:
df.dtypes

Sigla               object
Nome                object
Latitude           float64
Longitude          float64
Município           object
Modal               object
Rio                 object
Latitude_2         float64
Longitude_2        float64
OBS                 object
Considerar           int64
Carga_2023           int64
Carga_2024           int64
GN                 float64
GNL                float64
Conteineres/Ano    float64
dtype: object

# EDA

In [97]:
df.describe()

Latitude  Longitude  Latitude_2  Longitude_2  Considerar  \
count  86.000000  86.000000   86.000000    86.000000   96.000000   
mean   -3.773587 -63.488361   -3.778263   -63.564175    0.625000   
std     2.076320   4.406264    2.087978     4.343704    0.486664   
min    -8.747551 -72.581236   -8.747551   -72.581236    0.000000   
25%    -4.721653 -67.061608   -4.719700   -67.061608    0.000000   
50%    -3.354899 -62.973198   -3.350754   -63.020109    1.000000   
75%    -2.746235 -59.750366   -2.707575   -60.004683    1.000000   
max     1.190652 -56.668167    1.190652   -56.668167    1.000000   

          Carga_2023     Carga_2024            GN            GNL  \
count      96.000000      96.000000  8.200000e+01      82.000000   
mean    20103.364583   20673.541667  6.879314e+06   11465.524114   
std     31821.860685   32843.231021  1.043984e+07   17399.725018   
min         0.000000       0.000000  6.516820e+04     108.613667   
25%      1568.250000    1626.750000  7.980842e+05    1330.140293   
50%     10170.000000   10398.000000  3.806758e+06    6344.596973   
75%     21500.500000   22015.500000  7.134032e+06   11890.053804   
max    210942.000000  220434.000000  6.650596e+07  110843.264444   

       Conteineres/Ano  
count        82.000000  
mean        229.310482  
std         347.994500  
min           2.172273  
25%          26.602806  
50%         126.891939  
75%         237.801076  
max        2216.865289

In [98]:
df.Rio.value_counts(dropna=False)

Solimões    23
Negro       11
Madeira     11
Amazonas    11
NaN         10
Purus        9
--           9
Juruá        8
Japurá       3
Javari       1
Name: Rio, dtype: int64

In [99]:
df = df[~df.Rio.isin(['--'])]
df = df.dropna(subset=['Rio'])

## Mapa de demanda

In [100]:
# Topo map
filepath = 'https://raw.githubusercontent.com/tbrugz/geodata-br/master/geojson/geojs-13-mun.json'

topo = vg.Chart(filepath).mark_geoshape(
    stroke="#dd",
    strokeWidth=2.5,
    color="lightgray",
).project(
    type='mercator'
)

# Demanda
selection = vg.selection_multi(fields=['Rio'], bind='legend')
points = vg.Chart(df).mark_point().encode(
    vg.Longitude('Longitude:Q',
                ),
    vg.Latitude('Latitude:Q',
               ),
    color= vg.condition(selection,
                        vg.Color('Rio:N', scale=vg.Scale(scheme='set1')),
                        vg.value('lightgray'),
                       ),
    size=vg.Size('Conteineres/Ano:Q', 
                 scale=None,
                 legend=vg.Legend(title='Conteineres por Ano')),
    tooltip=['Sigla', 'Nome', 'Latitude', 'Longitude', 'Município', 'Modal', 'Rio',
             'Latitude_2', 'Longitude_2', 'OBS', 'Considerar', 'Carga_2023',
             'Carga_2024', 'GN', 'GNL', 'Conteineres/Ano']
)

# Mapa + Demanda + Configs
vg.layer(
    topo,
    points,
).properties(
    width=600,
    height=600,
).configure_title(
    fontSize=24,
).configure_axis(
    grid=False,
    labelFontSize=14,
    titleFontSize=20,
).configure_legend(
    titleFontSize=16,
    labelFontSize=14, 
).add_selection(
    selection
)

alt.LayerChart(...)

## Demanda (permite zoom e seleção na legenda)

In [101]:
selection = vg.selection_multi(fields=['Rio'], bind='legend')

chart = vg.Chart(df).mark_point().encode(
    vg.X('Longitude:Q',
          scale=vg.Scale(zero=False)
        ),
    vg.Y('Latitude:Q',
         scale=vg.Scale(zero=False)
        ),
    color= vg.condition(selection,
                        vg.Color('Rio:N', scale=vg.Scale(scheme='set1')),
                        vg.value('lightgray'),
                       ),
    size=vg.Size('Conteineres/Ano:Q', 
                 scale=None,
                 legend=vg.Legend(title='Conteineres por Ano')),
    tooltip=['Sigla', 'Nome', 'Latitude', 'Longitude', 'Município', 'Modal', 'Rio',
             'Latitude_2', 'Longitude_2', 'OBS', 'Considerar', 'Carga_2023',
             'Carga_2024', 'GN', 'GNL', 'Conteineres/Ano']
).properties(
    width=600,
    height=600,
).configure_title(
    fontSize=24,
).configure_axis(
    labelFontSize=14,
    titleFontSize=20,
).configure_legend(
    titleFontSize=16,
    labelFontSize=14, 
).add_selection(
    selection
).interactive()

chart

alt.Chart(...)

## Pareto

In [102]:
df_pareto = df.copy()
df_pareto = df_pareto[df_pareto['Conteineres/Ano'].notna()]
df_pareto = df_pareto.sort_values(by=['Conteineres/Ano'], ascending=False)

df_pareto["count cumsum"] = df_pareto['Conteineres/Ano'].cumsum()
df_pareto["cumpercentage"] = df_pareto["count cumsum"]/(df_pareto['Conteineres/Ano'].sum())

sort_order = df_pareto["Nome"].tolist()

selection = vg.selection_multi(fields=['Rio'], bind='legend')

# Create Base
base = vg.Chart(df_pareto).encode(
    vg.X("Nome:O",
         sort=sort_order),
).properties(
    width=800,
    height=600,
)
# Bars chart
bars = base.mark_bar().encode(
    vg.Y("Conteineres/Ano:Q",
    axis=vg.Axis(labelFontSize=15)
        ),
    color= vg.condition(selection,
                        vg.Color('Rio:N', scale=vg.Scale(scheme='set1')),
                        vg.value('lightgray'),
                       ),
).properties(
    width=800,
    height=600,
)
# Line chart
line = base.mark_line(strokeWidth=1.5, color="#cb4154" ).encode(
    vg.Y('cumpercentage:Q',
    title='Cumulative Count',
    axis=vg.Axis(format=".0%", labelFontSize=15, )
        ),
    text = vg.Text('cumpercentage:Q')
)
# Mark the percentage values on the line with Circle marks
points = base.mark_circle(strokeWidth= 3, color = "#cb4154").encode(
    vg.Y('cumpercentage:Q', axis=None),
    tooltip=['Nome', 'Município', 'Modal', 'Rio', 'OBS', 'Considerar', 'Conteineres/Ano'],
)

# Layer all the elements together 
(bars + line + points).resolve_scale(
    y = 'independent'
).configure_title(
    fontSize=24,
).configure_axis(
    grid=False,
    labelFontSize=10,
    titleFontSize=20,
).add_selection(
    selection
).interactive()

alt.LayerChart(...)

# Considerar

In [103]:
df.loc[df.Nome == 'ALTEROSA', 'Considerar'] = 0

In [104]:
# Topo map
filepath = 'https://raw.githubusercontent.com/tbrugz/geodata-br/master/geojson/geojs-13-mun.json'

topo = vg.Chart(filepath).mark_geoshape(
    stroke="#dd",
    strokeWidth=0.3,
    opacity=0.2,
    color="lightgray",
).project(
    type='mercator'
)

# Demanda
selection = vg.selection_multi(fields=['Rio'], bind='legend')
points = vg.Chart(df[(df.Considerar == 1) & (df.Nome != 'ALTEROSA') & (df.Rio != 'Japurá')]
                 ).mark_line(point=True, size=3).encode(
    vg.Longitude('Longitude:Q',
                ),
    vg.Latitude('Latitude:Q',
               ),
    color= vg.condition(selection,
                        vg.Color('Rio:N', scale=vg.Scale(scheme='set1')),
                        vg.value('lightgray'),
                       ),
    #size=vg.Size('Conteineres/Ano:Q', 
    #             scale=None,
    #             legend=vg.Legend(title='Conteineres por Ano')),
    tooltip=['Sigla', 'Nome', 'Latitude', 'Longitude', 'Município', 'Modal', 'Rio',
             'Latitude_2', 'Longitude_2', 'OBS', 'Considerar', 'Carga_2023',
             'Carga_2024', 'GN', 'GNL', 'Conteineres/Ano']
)

# Mapa + Demanda + Configs
vg.layer(
    topo,
    points,
).properties(
    width=600,
    height=600,
).configure_title(
    fontSize=24,
).configure_axis(
    grid=False,
    labelFontSize=14,
    titleFontSize=20,
).configure_legend(
    titleFontSize=16,
    labelFontSize=14, 
).add_selection(
    selection
)

alt.LayerChart(...)

A fazer:

[DONE] 1) Levantar a matriz de distâncias (Solimões, Madeira e Amazonas) para qualquer origem e destino

2) Calcular tempo de ciclo:

Tempo de ciclo = Tempo de Nav + Tempo de mov de carga

Tempo de Nav = distancia / vel. média

Tempo de Mov de carga = 4 x 5 min

(Demanda por ciclo de 14 dias, 14 dias, 7 dias) - dos nós extremos baseado na velocidade média (ajustado pra cima, múltiplos de 7 são convenientes)

- Tempo de Porto total é de 4 movimentos do conteiner (carreta)

- Estabelecer a frequência de entrega (1, 2, 3 vezes por ciclo)

- Demanda por entrega - aredondar por cima (= Demanda / frequencia)

3) Levantamento da capacidade de navios

4) Geração de rotas (itertools -Python) 
 
 - Limitar trechos entre Portos com alta distância (300 km - verificar qual limite)
 - Capacidade máxima do navio

# Distâncias

In [105]:
filepath = '../data/distancias.xlsx'
df_dist = pd.read_excel(filepath, index_col=0)

In [106]:
df_dist.style.format("{:.2f}").background_gradient('Blues')

# Definição do horizonte de planejamento

In [126]:
# Dataframe com apenas localidades consideradas e rios
rios = ['Amazonas', 'Madeira', 'Solimões']
df_sample = df[(df.Considerar == 1) & (df.Rio.isin(rios))]
df_sample = df_sample[['Rio', 'Nome', 'Conteineres/Ano']]

In [155]:
(35*50)/0.9

1944.4444444444443

In [153]:
400 / 50

8.0

In [162]:
# Parameters
vel_media = 10 * 1.852 # velocidade média do navio
t_carregamento = 4 * 5 / 60 # 5 minutos para cada movimento (4 movimentos por carga)
f_corredor = 0.9 # porcentagem da capacidade útil do navio
capac_navio_nominal = 2000 # capacidade nominal do navio em volume [m3]
capac_carga  = 50 # capacidade do conteiner em volume [m3]

# Frequencia de visitas específica por rio, ajustada pensando na capacidade do navio
freq_visitas = [2, 3, 2]

distancias_maximas_de_manaus = [458, 972.8, 2043]

In [163]:
# Capacidade do navio
capac_navio = (f_corredor * capac_navio_nominal) / capac_carga

for i in range(0, len(rios)):
    rio = rios[i]
    freq = freq_visitas[i]
    
    # Selecionar localidades "Consideradas" e de dado "Rio"
    df_sample_rio = df_sample[df_sample.Rio == rio]
    loc_rio = df_sample_rio['Nome'].tolist()
    # Maxima dist entre localidades (extremos)
    max_dist = distancias_maximas_de_manaus[i]

    # Tempo de Navegação é 2 vezes a distancia dividida pela vel 
    tempo_nav = 2 * max_dist / vel_media
    
    # Demanda total por ano (arredonda para cima)
    demanda_total = m.ceil(df_sample_rio['Conteineres/Ano'].sum())
    
    # Viagens redondas por ano (arredonda por cima)
    viagens_redondas = m.ceil(demanda_total / capac_navio)
    
    # Tempo de ciclo
    t_ciclo = (freq * tempo_nav + demanda_total/ (12 * 30 * 24) * t_carregamento)
    
    print(rio)
    print(f'Frequência de entrega: {freq} [-]')
    print(f'Distância máxima: {max_dist} [km]')
    print(f'Tempo de Navegação: {round(tempo_nav, 2)} [h]')
    print(f'Demanda total: {demanda_total} [cargas/ano]')
    print(f'Viagens redondas: {viagens_redondas} [viagens]')
    print(f'Tempo de ciclo: {round(t_ciclo, 2)} [h] ou {round(t_ciclo /24, 2)} [dias] \n')

Amazonas
Frequência de entrega: 2 [-]
Distância máxima: 458 [km]
Tempo de Navegação: 49.46 [h]
Demanda total: 4544 [cargas/ano]
Viagens redondas: 127 [viagens]
Tempo de ciclo: 99.1 [h] ou 4.13 [dias] 

Madeira
Frequência de entrega: 3 [-]
Distância máxima: 972.8 [km]
Tempo de Navegação: 105.05 [h]
Demanda total: 2493 [cargas/ano]
Viagens redondas: 70 [viagens]
Tempo de ciclo: 315.26 [h] ou 13.14 [dias] 

Solimões
Frequência de entrega: 2 [-]
Distância máxima: 2043 [km]
Tempo de Navegação: 220.63 [h]
Demanda total: 3428 [cargas/ano]
Viagens redondas: 96 [viagens]
Tempo de ciclo: 441.38 [h] ou 18.39 [dias] 



Os números apresentados justificam a extensão do horizonte de planejamento para cada rio: No Amazonas, o tempo de ciclo de 4.54 dias indica um horizonte de 7 dias; no rio Madeira,  o tempo de ciclo de 10.3 dias indica um horizonte de 14 dias, e no Solimões 21 dias.

# Frequência de visitas

In [145]:
def _tempo_de_ciclo(data):
    if data == 'Amazonas':
        return 7
    if data == 'Madeira':
        return 14
    if data == 'Solimões':
        return 21

In [146]:
df_sample['tempo_ciclo'] = df_sample.Rio.apply(_tempo_de_ciclo)

In [147]:
df_sample['demanda_por_ciclo'] = (df_sample['Conteineres/Ano'] / (12 * 30) * df_sample['tempo_ciclo'] ).apply(m.ceil)

# Simulando 1, 2, 3 ou 4 visitas por ciclo (para ver as aderencias e definir)
freqs_possiveis = [1, 2, 3, 4]
for f in freqs_possiveis:
    df_sample[f'demanda_{f}_visita'] = (df_sample['demanda_por_ciclo'] / f).apply(m.ceil)

df_sample[['Rio', 'Nome','demanda_1_visita', 'demanda_2_visita', 'demanda_3_visita', 'demanda_4_visita']]

Rio                   Nome  demanda_1_visita  demanda_2_visita  \
2   Solimões               CAMPINAS                 1                 1   
8   Solimões                CAIAMBÉ                 3                 2   
9   Solimões                   TEFÉ                60                30   
10  Solimões               ALVARÃES                 8                 4   
11  Solimões                 UARINI                 8                 4   
12  Solimões              FONTE BOA                13                 7   
13  Solimões                  JUTAÍ                13                 7   
14  Solimões              TONANTINS                 7                 4   
15  Solimões   SANTO ANTÔNIO DO IÇÁ                11                 6   
17  Solimões                AMATURÁ                 5                 3   
18  Solimões  SÃO PAULO DE OLIVENÇA                 9                 5   
19  Solimões    SANTA RITA DO WEILL                 3                 2   
20  Solimões      BELÉM DO SOLIMÕES                 2                 1   
21  Solimões                FEIJOAL                 1                 1   
22  Solimões      BENJAMIN CONSTANT                23                12   
23  Solimões              TABATINGA                43                22   
55   Madeira                AUTAZES                16                 8   
56   Madeira   NOVA OLINDA DO NORTE                13                 7   
57   Madeira                 AXINIM                 1                 1   
58   Madeira                  BORBA                12                 6   
59   Madeira          NOVO ARIPUANÃ                10                 5   
60   Madeira               MANICORÉ                15                 8   
61   Madeira            AUXILIADORA                 1                 1   
62   Madeira                HUMAITÁ                33                17   
75  Amazonas            ITACOATIARA                44                22   
76  Amazonas           NOVO REMANÇO                 7                 4   
77  Amazonas            URUCURITUBA                 5                 3   
78  Amazonas     AUGUSTO MONTENEGRO                 1                 1   
79  Amazonas                URUCARÁ                 4                 2   
80  Amazonas              PARINTINS                29                15   
82  Amazonas          VILA AMAZÔNIA                 2                 1   

    demanda_3_visita  demanda_4_visita  
2                  1                 1  
8                  1                 1  
9                 20                15  
10                 3                 2  
11                 3                 2  
12                 5                 4  
13                 5                 4  
14                 3                 2  
15                 4                 3  
17                 2                 2  
18                 3                 3  
19                 1                 1  
20                 1                 1  
21                 1                 1  
22                 8                 6  
23                15                11  
55                 6                 4  
56                 5                 4  
57                 1                 1  
58                 4                 3  
59                 4                 3  
60                 5                 4  
61                 1                 1  
62                11                 9  
75                15                11  
76                 3                 2  
77                 2                 2  
78                 1                 1  
79                 2                 1  
80                10                 8  
82                 1                 1

In [148]:
# Observando qual demanda por visita parece razoavel:
freq_visita = {'CAMPINAS': 1,
 'CAIAMBÉ': 1,
 'TEFÉ': 4,
 'ALVARÃES': 1,
 'UARINI': 1,
 'FONTE BOA': 2,
 'JUTAÍ': 2,
 'TONANTINS': 1,
 'SANTO ANTÔNIO DO IÇÁ': 1,
 'AMATURÁ': 1,
 'SÃO PAULO DE OLIVENÇA': 1,
 'SANTA RITA DO WEILL': 1,
 'BELÉM DO SOLIMÕES': 1,
 'FEIJOAL': 1,
 'BENJAMIN CONSTANT': 3,
 'TABATINGA': 4,
 'AUTAZES': 2,
 'NOVA OLINDA DO NORTE': 2,
 'AXINIM': 1,
 'BORBA': 2,
 'NOVO ARIPUANÃ': 1,
 'MANICORÉ': 2,
 'AUXILIADORA': 1,
 'HUMAITÁ': 3,
 'ITACOATIARA': 4,
 'NOVO REMANÇO': 1,
 'URUCURITUBA': 1,
 'AUGUSTO MONTENEGRO': 1,
 'URUCARÁ': 1,
 'PARINTINS': 3,
 'VILA AMAZÔNIA': 1
              }

In [149]:
def _demanda_por_visita(data):
    return data[data[4] - 1]

In [150]:
# Mapear frequencias observadas
df_sample['freq_visita'] = df_sample['Nome'].map(freq_visita)
df_sample['demanda_por_visita'] = df_sample.iloc[:, -5:].apply(_demanda_por_visita, axis=1)

In [152]:
df_sample[['Nome', 'Rio', 'freq_visita']]

Nome       Rio  freq_visita
2                CAMPINAS  Solimões            1
8                 CAIAMBÉ  Solimões            1
9                    TEFÉ  Solimões            4
10               ALVARÃES  Solimões            1
11                 UARINI  Solimões            1
12              FONTE BOA  Solimões            2
13                  JUTAÍ  Solimões            2
14              TONANTINS  Solimões            1
15   SANTO ANTÔNIO DO IÇÁ  Solimões            1
17                AMATURÁ  Solimões            1
18  SÃO PAULO DE OLIVENÇA  Solimões            1
19    SANTA RITA DO WEILL  Solimões            1
20      BELÉM DO SOLIMÕES  Solimões            1
21                FEIJOAL  Solimões            1
22      BENJAMIN CONSTANT  Solimões            3
23              TABATINGA  Solimões            4
55                AUTAZES   Madeira            2
56   NOVA OLINDA DO NORTE   Madeira            2
57                 AXINIM   Madeira            1
58                  BORBA   Madeira            2
59          NOVO ARIPUANÃ   Madeira            1
60               MANICORÉ   Madeira            2
61            AUXILIADORA   Madeira            1
62                HUMAITÁ   Madeira            3
75            ITACOATIARA  Amazonas            4
76           NOVO REMANÇO  Amazonas            1
77            URUCURITUBA  Amazonas            1
78     AUGUSTO MONTENEGRO  Amazonas            1
79                URUCARÁ  Amazonas            1
80              PARINTINS  Amazonas            3
82          VILA AMAZÔNIA  Amazonas            1

# Geração de Rotas

- Gerar todas as combinações de localidades (contendo 1, 2, 3, 4, etc.) para cada rio, até que a capacidade do navio se esgote (Ter as localidades ordenadas em ordem crescente de distância a Manaus).
- A cada rota, registrar:
    - tempo de ciclo da rota (separado por tempo navegando e tempo de porto)
    - demanda total da rota,
    - custo de navegação da rota
    - se a localidade i está na rota r ou não

## Loop principal

In [23]:
# Capacidade maxima da embarcacao
cap_max = 35
vel_media = 10 * 1.852 # velocidade média do navio
t_carregamento = 4 * 5 / 60 # 5 minutos para cada movimento (4 movimentos por carga)

In [24]:
def make_route(data: pd.DataFrame, 
               matrix_distancias: pd.DataFrame, 
               rio: str) -> pd.DataFrame:
    
    # Ordenar localidades por distancia a Manaus
    lista_localidades = data[data.Rio == rio]['Nome'].tolist()
    localidades_ordenadas = matrix_distancias.loc[lista_localidades].sort_values('MANAUS').index.tolist()
    
    localidades =  data.set_index('Nome').loc[localidades_ordenadas].index.tolist()
    demandas = data.set_index('Nome').loc[localidades_ordenadas]['demanda_por_visita'].tolist()
    
    rotas = []
    demandas_rotas = []

    distancias_manaus = []
    tempos_porto = []
    tempos_nav = []
    tempos_ciclo = []

    num_rotas_totais = 0

    for i in range(1, len(localidades) + 1): # Para cada combinacao (1 a 1, 2 a 2....)
        print(f'Combinações {i} a {i}:')
        comb_demandas = list(combinations(demandas,i))
        comb_locais = list(combinations(localidades,i))

        target_capac_max = 0
        for j, demanda_comb in enumerate(comb_demandas): # Para cada rota nas combinacoes
            demanda_comb = sum(demanda_comb)
            if demanda_comb <= cap_max: # se atingir a capacidade maxiam do navio
                print(f'Demanda total da rota: {demanda_comb}')
                demandas_rotas.append(demanda_comb)

                target_capac_max +=1
                # Estabelecer os nos da combinacao
                nos_comb = list(comb_locais[j])
                print(f'Rota: {nos_comb}')
                rotas.append(nos_comb)

                dist_manaus = 0
                dist_manaus += df_dist.loc[nos_comb[0], 'MANAUS']
                final = df_dist.loc[nos_comb[-1], 'MANAUS']
                print(f'Distância do Primeiro local até Manaus: {dist_manaus}')
                print(f'Distância último local até Manaus: {final}')
                for k in range(0, len(nos_comb)):
                    if k < len(nos_comb) - 1:
                        no_anterior = nos_comb[k]
                        no_posterior = nos_comb[k+1]
                        distancia_entre_nos = df_dist.loc[no_anterior, no_posterior]
                        print(f'Arcos: {no_anterior} + {no_posterior}')
                        print(f'Distância do arco: {distancia_entre_nos}')
                        dist_manaus += distancia_entre_nos

                dist_manaus = round(dist_manaus, 2)
                print(f'Distância percorrida: {round(dist_manaus,2)}')
                distancias_manaus.append(dist_manaus)

                tempo_porto = round(demanda_comb * t_carregamento, 2)
                tempo_nav = round(2 * dist_manaus / vel_media, 2)
                tempo_ciclo = round(tempo_porto + tempo_nav, 2)

                print(f'Tempo de porto: {tempo_porto}')
                tempos_porto.append(tempo_porto)
                print(f'Tempo de nav: {tempo_nav}')
                tempos_nav.append(tempo_nav)
                print(f'Tempo de ciclo: {tempo_ciclo}')
                tempos_ciclo.append(tempo_ciclo)

                print('*******************************************')
        print(f'Total de rotas com {i} localidades: {target_capac_max}')
        num_rotas_totais += target_capac_max
        print('-------------------------------------------------')

        if target_capac_max == 0:
            print('Não há combinações maiores possíveis\n')
            break

    print(f'Número total de rotas: {num_rotas_totais}\n')
    print(f'Lista de rotas: {rotas}\n')
    print(f'Demanda [containers] das rotas: {demandas_rotas}\n')
    print(f'Tempo [h] de porto das rotas: {tempos_porto}')
    print(f'Tempo [h] de navegação nas rotas: {tempos_nav}')
    print(f'Tempo [h] de ciclo nas rotas: {tempos_ciclo}')
    print(f'Distâncias máximas até Manaus: {distancias_manaus}')
    
    dict_to_dataframe = {
    'nos': pd.Series(rotas),
    'demanda': pd.Series(demandas_rotas),
    'tempo_porto': pd.Series(tempos_porto),
    'tempo_nav': pd.Series(tempos_nav),
    'tempo_ciclo': pd.Series(tempos_ciclo),
    'distancia': pd.Series(distancias_manaus)
}
    
    rotas = pd.DataFrame.from_dict(dict_to_dataframe, orient='index').T
    rotas['vetor_loc_rota'] = rotas['nos'].apply(vetor_no_pertence_a_rota)
    
    return rotas

In [25]:
# Escolha o rio que quer gerar as rotas
rio = 'Solimões'  # 'Amazonas', 'Madeira', 'Solimões'

rota = make_route(data=df_sample, 
                  matrix_distancias=df_dist,
                  rio=rio)

Combinações 1 a 1:
Demanda total da rota: 1
Rota: ['CAMPINAS']
Distância do Primeiro local até Manaus: 181.0
Distância último local até Manaus: 181.0
Distância percorrida: 181.0
Tempo de porto: 0.33
Tempo de nav: 19.55
Tempo de ciclo: 19.88
*******************************************
Demanda total da rota: 3
Rota: ['CAIAMBÉ']
Distância do Primeiro local até Manaus: 596.0
Distância último local até Manaus: 596.0
Distância percorrida: 596.0
Tempo de porto: 1.0
Tempo de nav: 64.36
Tempo de ciclo: 65.36
*******************************************
Demanda total da rota: 15
Rota: ['TEFÉ']
Distância do Primeiro local até Manaus: 1183.3
Distância último local até Manaus: 1183.3
Distância percorrida: 1183.3
Tempo de porto: 5.0
Tempo de nav: 127.79
Tempo de ciclo: 132.79
*******************************************
Demanda total da rota: 8
Rota: ['ALVARÃES']
Distância do Primeiro local até Manaus: 1200.95
Distância último local até Manaus: 1200.95
Distância percorrida: 1200.95
Tempo de porto: 2.6

Distância do Primeiro local até Manaus: 181.0
Distância último local até Manaus: 1746.6
Arcos: CAMPINAS + FONTE BOA
Distância do arco: 813.75
Arcos: FONTE BOA + AMATURÁ
Distância do arco: 337.45
Distância percorrida: 1332.2
Tempo de porto: 4.33
Tempo de nav: 143.87
Tempo de ciclo: 148.2
*******************************************
Demanda total da rota: 17
Rota: ['CAMPINAS', 'FONTE BOA', 'SÃO PAULO DE OLIVENÇA']
Distância do Primeiro local até Manaus: 181.0
Distância último local até Manaus: 1833.45
Arcos: CAMPINAS + FONTE BOA
Distância do arco: 813.75
Arcos: FONTE BOA + SÃO PAULO DE OLIVENÇA
Distância do arco: 424.3
Distância percorrida: 1419.05
Tempo de porto: 5.67
Tempo de nav: 153.25
Tempo de ciclo: 158.92
*******************************************
Demanda total da rota: 11
Rota: ['CAMPINAS', 'FONTE BOA', 'SANTA RITA DO WEILL']
Distância do Primeiro local até Manaus: 181.0
Distância último local até Manaus: 1884.15
Arcos: CAMPINAS + FONTE BOA
Distância do arco: 813.75
Arcos: FONTE 

Arcos: TEFÉ + JUTAÍ
Distância do arco: 348.65
Arcos: JUTAÍ + FEIJOAL
Distância do arco: 470.95
Distância percorrida: 2002.9
Tempo de porto: 7.67
Tempo de nav: 216.3
Tempo de ciclo: 223.97
*******************************************
Demanda total da rota: 33
Rota: ['TEFÉ', 'JUTAÍ', 'TABATINGA']
Distância do Primeiro local até Manaus: 1183.3
Distância último local até Manaus: 2043.8
Arcos: TEFÉ + JUTAÍ
Distância do arco: 348.65
Arcos: JUTAÍ + TABATINGA
Distância do arco: 522.6
Distância percorrida: 2054.55
Tempo de porto: 11.0
Tempo de nav: 221.87
Tempo de ciclo: 232.87
*******************************************
Demanda total da rota: 30
Rota: ['TEFÉ', 'JUTAÍ', 'BENJAMIN CONSTANT']
Distância do Primeiro local até Manaus: 1183.3
Distância último local até Manaus: 2045.9
Arcos: TEFÉ + JUTAÍ
Distância do arco: 348.65
Arcos: JUTAÍ + BENJAMIN CONSTANT
Distância do arco: 524.7
Distância percorrida: 2056.65
Tempo de porto: 10.0
Tempo de nav: 222.1
Tempo de ciclo: 232.1
************************

Distância percorrida: 2046.55
Tempo de porto: 7.33
Tempo de nav: 221.01
Tempo de ciclo: 228.34
*******************************************
Demanda total da rota: 25
Rota: ['FONTE BOA', 'TONANTINS', 'SANTO ANTÔNIO DO IÇÁ']
Distância do Primeiro local até Manaus: 1409.75
Distância último local até Manaus: 1694.7
Arcos: FONTE BOA + TONANTINS
Distância do arco: 251.95
Arcos: TONANTINS + SANTO ANTÔNIO DO IÇÁ
Distância do arco: 34.1
Distância percorrida: 1695.8
Tempo de porto: 8.33
Tempo de nav: 183.13
Tempo de ciclo: 191.46
*******************************************
Demanda total da rota: 19
Rota: ['FONTE BOA', 'TONANTINS', 'AMATURÁ']
Distância do Primeiro local até Manaus: 1409.75
Distância último local até Manaus: 1746.6
Arcos: FONTE BOA + TONANTINS
Distância do arco: 251.95
Arcos: TONANTINS + AMATURÁ
Distância do arco: 86.0
Distância percorrida: 1747.7
Tempo de porto: 6.33
Tempo de nav: 188.74
Tempo de ciclo: 195.07
*******************************************
Demanda total da rota: 23
R

*******************************************
Demanda total da rota: 11
Rota: ['FONTE BOA', 'SANTA RITA DO WEILL', 'FEIJOAL']
Distância do Primeiro local até Manaus: 1409.75
Distância último local até Manaus: 1992.15
Arcos: FONTE BOA + SANTA RITA DO WEILL
Distância do arco: 475.0
Arcos: SANTA RITA DO WEILL + FEIJOAL
Distância do arco: 108.05
Distância percorrida: 1992.8
Tempo de porto: 3.67
Tempo de nav: 215.21
Tempo de ciclo: 218.88
*******************************************
Demanda total da rota: 21
Rota: ['FONTE BOA', 'SANTA RITA DO WEILL', 'TABATINGA']
Distância do Primeiro local até Manaus: 1409.75
Distância último local até Manaus: 2043.8
Arcos: FONTE BOA + SANTA RITA DO WEILL
Distância do arco: 475.0
Arcos: SANTA RITA DO WEILL + TABATINGA
Distância do arco: 159.7
Distância percorrida: 2044.45
Tempo de porto: 7.0
Tempo de nav: 220.78
Tempo de ciclo: 227.78
*******************************************
Demanda total da rota: 18
Rota: ['FONTE BOA', 'SANTA RITA DO WEILL', 'BENJAMIN CON

...

Demanda total da rota: 35
Rota: ['CAIAMBÉ', 'JUTAÍ', 'TONANTINS', 'AMATURÁ', 'SANTA RITA DO WEILL', 'BELÉM DO SOLIMÕES', 'BENJAMIN CONSTANT']
Distância do Primeiro local até Manaus: 596.0
Distância último local até Manaus: 2045.9
Arcos: CAIAMBÉ + JUTAÍ
Distância do arco: 379.15
Arcos: JUTAÍ + TONANTINS
Distância do arco: 139.9
Arcos: TONANTINS + AMATURÁ
Distância do arco: 86.0
Arcos: AMATURÁ + SANTA RITA DO WEILL
Distância do arco: 138.05
Arcos: SANTA RITA DO WEILL + BELÉM DO SOLIMÕES
Distância do arco: 63.55
Arcos: BELÉM DO SOLIMÕES + BENJAMIN CONSTANT
Distância do arco: 98.75
Distância percorrida: 1501.4
Tempo de porto: 11.67
Tempo de nav: 162.14
Tempo de ciclo: 173.81
*******************************************
Demanda total da rota: 34
Rota: ['CAIAMBÉ', 'JUTAÍ', 'TONANTINS', 'AMATURÁ', 'SANTA RITA DO WEILL', 'FEIJOAL', 'BENJAMIN CONSTANT']
Distância do Primeiro local até Manaus: 596.0
Distância último local até Manaus: 2045.9
Arcos: CAIAMBÉ + JUTAÍ
Distância do arco: 379.15
Arcos: 

Tempo de ciclo: 182.19
*******************************************
Demanda total da rota: 34
Rota: ['CAMPINAS', 'CAIAMBÉ', 'ALVARÃES', 'JUTAÍ', 'TONANTINS', 'AMATURÁ', 'BELÉM DO SOLIMÕES', 'FEIJOAL']
Distância do Primeiro local até Manaus: 181.0
Distância último local até Manaus: 1992.15
Arcos: CAMPINAS + CAIAMBÉ
Distância do arco: 546.8
Arcos: CAIAMBÉ + ALVARÃES
Distância do arco: 58.85
Arcos: ALVARÃES + JUTAÍ
Distância do arco: 320.4
Arcos: JUTAÍ + TONANTINS
Distância do arco: 139.9
Arcos: TONANTINS + AMATURÁ
Distância do arco: 86.0
Arcos: AMATURÁ + BELÉM DO SOLIMÕES
Distância do arco: 201.55
Arcos: BELÉM DO SOLIMÕES + FEIJOAL
Distância do arco: 45.0
Distância percorrida: 1579.5
Tempo de porto: 11.33
Tempo de nav: 170.57
Tempo de ciclo: 181.9
*******************************************
Demanda total da rota: 32
Rota: ['CAMPINAS', 'CAIAMBÉ', 'ALVARÃES', 'JUTAÍ', 'TONANTINS', 'SANTA RITA DO WEILL', 'BELÉM DO SOLIMÕES', 'FEIJOAL']
Distância do Primeiro local até Manaus: 181.0
Distância 

Demanda total da rota: 35
Rota: ['CAMPINAS', 'CAIAMBÉ', 'UARINI', 'FONTE BOA', 'TONANTINS', 'AMATURÁ', 'SANTA RITA DO WEILL', 'FEIJOAL']
Distância do Primeiro local até Manaus: 181.0
Distância último local até Manaus: 1992.15
Arcos: CAMPINAS + CAIAMBÉ
Distância do arco: 546.8
Arcos: CAIAMBÉ + UARINI
Distância do arco: 101.45
Arcos: UARINI + FONTE BOA
Distância do arco: 166.8
Arcos: FONTE BOA + TONANTINS
Distância do arco: 251.95
Arcos: TONANTINS + AMATURÁ
Distância do arco: 86.0
Arcos: AMATURÁ + SANTA RITA DO WEILL
Distância do arco: 138.05
Arcos: SANTA RITA DO WEILL + FEIJOAL
Distância do arco: 108.05
Distância percorrida: 1580.1
Tempo de porto: 11.67
Tempo de nav: 170.64
Tempo de ciclo: 182.31
*******************************************
Demanda total da rota: 34
Rota: ['CAMPINAS', 'CAIAMBÉ', 'UARINI', 'FONTE BOA', 'TONANTINS', 'AMATURÁ', 'BELÉM DO SOLIMÕES', 'FEIJOAL']
Distância do Primeiro local até Manaus: 181.0
Distância último local até Manaus: 1992.15
Arcos: CAMPINAS + CAIAMBÉ
D

Distância do arco: 63.55
Arcos: BELÉM DO SOLIMÕES + FEIJOAL
Distância do arco: 45.0
Distância percorrida: 1579.4
Tempo de porto: 11.33
Tempo de nav: 170.56
Tempo de ciclo: 181.89
*******************************************
Demanda total da rota: 35
Rota: ['CAMPINAS', 'ALVARÃES', 'FONTE BOA', 'AMATURÁ', 'SANTA RITA DO WEILL', 'BELÉM DO SOLIMÕES', 'FEIJOAL', 'BENJAMIN CONSTANT']
Distância do Primeiro local até Manaus: 181.0
Distância último local até Manaus: 2045.9
Arcos: CAMPINAS + ALVARÃES
Distância do arco: 604.95
Arcos: ALVARÃES + FONTE BOA
Distância do arco: 208.9
Arcos: FONTE BOA + AMATURÁ
Distância do arco: 337.45
Arcos: AMATURÁ + SANTA RITA DO WEILL
Distância do arco: 138.05
Arcos: SANTA RITA DO WEILL + BELÉM DO SOLIMÕES
Distância do arco: 63.55
Arcos: BELÉM DO SOLIMÕES + FEIJOAL
Distância do arco: 45.0
Arcos: FEIJOAL + BENJAMIN CONSTANT
Distância do arco: 53.85
Distância percorrida: 1632.75
Tempo de porto: 11.67
Tempo de nav: 176.32
Tempo de ciclo: 187.99
***********************

NameError: name 'vetor_no_pertence_a_rota' is not defined

In [ ]:
rota

In [ ]:
# Salvar a base
folderpath_rotas = '../data/rotas/'
rotas.to_parquet(folderpath_rotas + f'rotas_{rio}.parquet')